In [3]:
from keras.preprocessing.image import ImageDataGenerator
from keras import layers
from keras import models
from keras import optimizers
#from tensorflow.keras.preprocessing import image
import os
from sklearn.model_selection import train_test_split
import shutil
import random
import math
import numpy as np
import zipfile
import pandas as pd
import matplotlib.image as mpimg
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from datetime import datetime
from tensorflow import keras
from sklearn.metrics import confusion_matrix, classification_report
import sklearn.metrics as skm
import itertools
import numpy as np
import matplotlib.pyplot as plt

In [169]:
def prepare_dataset(X_dataset, y_dataset, classes, n_samples):
    if n_samples is None:
        img_samples = X_dataset.shape[0]
    else:
        img_samples = n_samples

    df_aux = pd.DataFrame(columns=['id', 'label'])

    list_aux = []

    for i in range(img_samples):
        nm_file = str(i)+'-'+str([classes[x] for x in y_dataset[i]]).strip('[]').strip('\'')+'.'+'png'
        sample = {'id':nm_file, 'label':str([classes[x] for x in y_dataset[i]]).strip('[]').strip('\'')}
        list_aux.append(sample)

    return pd.concat([df_aux, pd.DataFrame(list_aux)], ignore_index=True)

In [170]:
def create_files(X_dataset, y_dataset, classes, dir, n_samples):
    if n_samples is None:
        img_samples = X_dataset.shape[0]
    else:
        img_samples = n_samples

    for i in range(img_samples):
        nm_file = str(i)+'-'+str([classes[x] for x in y_dataset[i]]).strip('[]').strip('\'')+'.'+'png'
        img = X_dataset[i]
        plt.imsave(dir + nm_file, img)

In [4]:
def create_directory(dir):
    if os.path.exists(dir):
        for file in os.listdir(dir):
            os.remove(dir+file)
    else:
        os.makedirs(dir)

In [172]:
from keras.datasets import cifar10

(X_train, y_train), (X_test, y_test) = cifar10.load_data()

cifar10_classes = ['airplane', 'automobile', 'bird', 'cat', 'deer', 'dog', 'frog', 'horse', 'ship', 'truck']

In [5]:
train_dir = "./train/"
test_dir = "./test/" 

create_directory(train_dir)
create_directory(test_dir)

In [174]:
train_samples = 1000 #X_train.shape[0]

create_files(X_train, y_train, cifar10_classes, train_dir, train_samples)

train_df = prepare_dataset(X_train, y_train, cifar10_classes, train_samples)

train_df.head()

id       label
0        0-frog.png        frog
1       1-truck.png       truck
2       2-truck.png       truck
3        3-deer.png        deer
4  4-automobile.png  automobile

In [175]:
test_samples = 50 #X_test.shape[0]

create_files(X_test, y_test, cifar10_classes, test_dir, test_samples)

test_df = prepare_dataset(X_test, y_test, cifar10_classes, test_samples)

test_df.head()

id     label
0       0-cat.png       cat
1      1-ship.png      ship
2      2-ship.png      ship
3  3-airplane.png  airplane
4      4-frog.png      frog

In [176]:
print('Total de imagens para treinamento: %s' % len(os.listdir(train_dir)))
print('Total de imagens para teste      : %s' % len(os.listdir(test_dir)))

Total de imagens para treinamento: 1000
Total de imagens para teste      : 50


In [188]:
train_datagen=ImageDataGenerator(rescale=1.0/255.0,
                                validation_split=0.25)

train_generator=train_datagen.flow_from_dataframe(
dataframe=train_df,
directory=train_dir,
x_col="id",
y_col="label",
subset="training",
batch_size=32,
seed=42,
shuffle=True,
class_mode="categorical",
target_size=(32,32))

valid_generator=train_datagen.flow_from_dataframe(
dataframe=train_df,
directory=train_dir,
x_col="id",
y_col="label",
subset="validation",
batch_size=32,
seed=42,
shuffle=True,
class_mode="categorical",
target_size=(32,32))

Found 750 validated image filenames belonging to 10 classes.
Found 250 validated image filenames belonging to 10 classes.


In [190]:
test_datagen=ImageDataGenerator(rescale=1.0/255.0)

test_generator=test_datagen.flow_from_dataframe(
dataframe=test_df,
directory=test_dir,
x_col="id",
y_col="label",
batch_size=32,
seed=42,
shuffle=False,
class_mode="categorical",
target_size=(32,32))

Found 50 validated image filenames belonging to 10 classes.


In [191]:
model = models.Sequential()
model.add(layers.Conv2D(32, (3, 3), padding='same', input_shape=(32,32,3), activation=('relu')))
model.add(layers.MaxPooling2D(pool_size=(2, 2)))

model.add(layers.Conv2D(64, (3, 3), padding='same', activation=('relu')))
model.add(layers.MaxPooling2D(pool_size=(2, 2)))

model.add(layers.Conv2D(128, (3, 3), padding='same', activation=('relu')))
model.add(layers.MaxPooling2D(pool_size=(2, 2)))

model.add(layers.Conv2D(128, (3, 3), padding='same', activation=('relu')))
model.add(layers.MaxPooling2D(pool_size=(2, 2)))

model.add(layers.Flatten())
model.add(layers.Dropout(0.25))
model.add(layers.Dense(512, activation='relu'))
model.add(layers.Dropout(0.25))
model.add(layers.Dense(10, activation='softmax'))

model.summary()

Model: "sequential_9"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d_36 (Conv2D)          (None, 32, 32, 32)        896       
                                                                 
 max_pooling2d_36 (MaxPoolin  (None, 16, 16, 32)       0         
 g2D)                                                            
                                                                 
 conv2d_37 (Conv2D)          (None, 16, 16, 64)        18496     
                                                                 
 max_pooling2d_37 (MaxPoolin  (None, 8, 8, 64)         0         
 g2D)                                                            
                                                                 
 conv2d_38 (Conv2D)          (None, 8, 8, 128)         73856     
                                                                 
 max_pooling2d_38 (MaxPoolin  (None, 4, 4, 128)       

In [192]:
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

In [193]:
train_step_size = train_generator.n//train_generator.batch_size
validation_step_size = valid_generator.n//valid_generator.batch_size

model.fit_generator(generator=train_generator,
          steps_per_epoch=train_step_size,
          validation_data=valid_generator,
          validation_steps=validation_step_size,
          epochs=5
)

C:\Users\User\AppData\Local\Temp\ipykernel_7464\2065233286.py:4: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  model.fit_generator(generator=train_generator,


Epoch 1/5
23/23 [==============================] - 12s 174ms/step - loss: 2.2994 - accuracy: 0.0864 - val_loss: 2.2741 - val_accuracy: 0.0714
Epoch 2/5
23/23 [==============================] - 4s 174ms/step - loss: 2.1586 - accuracy: 0.1992 - val_loss: 2.0836 - val_accuracy: 0.2098
Epoch 3/5
23/23 [==============================] - 3s 137ms/step - loss: 2.0665 - accuracy: 0.1992 - val_loss: 1.9916 - val_accuracy: 0.2455
Epoch 4/5
23/23 [==============================] - 4s 173ms/step - loss: 1.9621 - accuracy: 0.2549 - val_loss: 1.8165 - val_accuracy: 0.3482
Epoch 5/5
23/23 [==============================] - 3s 137ms/step - loss: 1.8831 - accuracy: 0.2799 - val_loss: 1.9023 - val_accuracy: 0.2902


In [194]:
count = 0
y_pred = list()
y_true = list()
class_names = cifar10_classes

# Loop do data generator de teste que contem as imagens
for batch in test_generator:
    
    # Pegando a imagem e o label
    images = batch[0]
    labels = batch[1]

    # Previsão
    predictions = model.predict(images)

    # Visualização da imagem
    for i in range(len(images)):
        
        image = images[i]
        label = labels[i]

        prediction = predictions[i]
    
        # Converte o array de previsão para visualizar a classe e a probabilidade
        predicted_class = np.argmax(prediction)
        probability = prediction[predicted_class]
        label = class_names[int(label)]
        y_true.append(label)

        # Faz o DE-PARA da probabilidade com o tipo de classe da previsão
        class_name = 'dog' if prediction >= 0.5 else 'cat'
        y_pred.append(class_name)
    
        # Configura a saída das imagens que serão visualizadas
        plt.imshow(images[i])
        plt.axis('Off')
        plt.show()
    
        # Imprime os resultados da classificação das images
        print("Label: ", label)
        print("Previsão: ", class_name) 
        print("Probabilidade: ", probability) 

1/1 [==============================] - 0s 431ms/step
[[[0.61960787 0.43921572 0.19215688]
  [0.62352943 0.43529415 0.18431373]
  [0.64705884 0.454902   0.20000002]
  ...
  [0.5372549  0.37254903 0.14117648]
  [0.49411768 0.35686275 0.14117648]
  [0.454902   0.33333334 0.12941177]]

 [[0.59607846 0.43921572 0.20000002]
  [0.5921569  0.43137258 0.15686275]
  [0.62352943 0.44705886 0.1764706 ]
  ...
  [0.53333336 0.37254903 0.12156864]
  [0.4901961  0.35686275 0.1254902 ]
  [0.4666667  0.34509805 0.13333334]]

 [[0.5921569  0.43137258 0.18431373]
  [0.5921569  0.427451   0.12941177]
  [0.61960787 0.43529415 0.14117648]
  ...
  [0.54509807 0.38431376 0.13333334]
  [0.50980395 0.37254903 0.13333334]
  [0.47058827 0.34901962 0.12941177]]

 ...

 [[0.26666668 0.48627454 0.69411767]
  [0.16470589 0.3921569  0.5803922 ]
  [0.12156864 0.34509805 0.5372549 ]
  ...
  [0.14901961 0.3803922  0.57254905]
  [0.0509804  0.2509804  0.42352945]
  [0.15686275 0.33333334 0.49803925]]

 [[0.2392157  0.45490

In [182]:
loss, accuracy = model.evaluate_generator(generator=valid_generator)
print("Test: accuracy = %f  ;  loss = %f " % (accuracy, loss))

C:\Users\User\AppData\Local\Temp\ipykernel_7464\2877989580.py:1: UserWarning: `Model.evaluate_generator` is deprecated and will be removed in a future version. Please use `Model.evaluate`, which supports generators.
  loss, accuracy = model.evaluate_generator(generator=valid_generator)


Test: accuracy = 0.432000  ;  loss = 2.053282 


In [183]:
test_generator.reset()
pred=model.predict_generator(test_generator)

predicted_class_indices=np.argmax(pred,axis=1)

C:\Users\User\AppData\Local\Temp\ipykernel_7464\369416828.py:2: UserWarning: `Model.predict_generator` is deprecated and will be removed in a future version. Please use `Model.predict`, which supports generators.
  pred=model.predict_generator(test_generator)


In [184]:
labels = (train_generator.class_indices)
labels = dict((v,k) for k,v in labels.items())
predictions = [labels[k] for k in predicted_class_indices]

In [185]:
filenames=test_generator.filenames
results=pd.DataFrame({"Filename":filenames,
                      "Predictions":predictions})
results.to_csv("results.csv",index=False)